<center> <img src = https://raw.githubusercontent.com/AndreyRysistov/DatasetsForPandas/main/hh%20label.jpg alt="drawing" style="width:400px;">

# <center> Проект: Анализ вакансий из HeadHunter
   

In [1]:
import pandas as pd
import psycopg2
import plotly.express as px
import requests
from bs4 import BeautifulSoup

In [3]:
connection = psycopg2.connect(
    dbname=DBNAME,
    user=USER,
    host=HOST,
    password=PASSWORD,
    port=PORT
)

# Юнит 3. Предварительный анализ данных

1. Напишите запрос, который посчитает количество вакансий в нашей базе (вакансии находятся в таблице vacancies). 

In [4]:
# используем агрегатную функцию count 
# для подсчета строк в таблице с вакансиями
query_3_1 = f'''select count(*)
    from vacancies 
'''

In [5]:
df = pd.read_sql_query(query_3_1, connection)
print(f"В базе {df['count'].iloc[0]} вакансий")

В базе 49197 вакансий


/tmp/ipykernel_48748/192670474.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_3_1, connection)


2. Напишите запрос, который посчитает количество работодателей (таблица employers). 

In [6]:
# используем агрегатную функцию count 
# для подсчета строк в таблице с работодателями
query_3_2 = f'''select count(*)
    from employers
'''

In [7]:
df = pd.read_sql_query(query_3_2, connection)
print(f"В базе {df['count'].iloc[0]} работодателей")

В базе 23501 работодателей


/tmp/ipykernel_48748/1705718816.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_3_2, connection)


3. Посчитате с помощью запроса количество регионов (таблица areas).

In [8]:
# используем агрегатную функцию count 
# для подсчета строк в таблице с регионами
query_3_3 = f'''select count(*)
    from areas
'''

In [9]:
df = pd.read_sql_query(query_3_3, connection)
print(f"В базе {df['count'].iloc[0]} региона")

В базе 1362 региона


/tmp/ipykernel_48748/1013547921.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_3_3, connection)


4. Посчитате с помощью запроса количество сфер деятельности в базе (таблица industries).

In [10]:
# используем агрегатную функцию count 
# для подсчета строк в таблице со сферами деятельности
query_3_4 = f'''select count(*)
    from industries
'''

In [11]:
df = pd.read_sql_query(query_3_4, connection)
print(f"В базе {df['count'].iloc[0]} сферы деятельности")

В базе 294 сферы деятельности


/tmp/ipykernel_48748/3611287681.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_3_4, connection)


***

### *Выводы по предварительному анализу данных*

- *База данных представляет собой набор таблиц, часть из которых связана друг с другом ключами (столбцами по которым возможно соединение таблиц).*
- *Таблица с вакансиями имеет наибольшее число признаков и является основным источником для анализа.*
- *В среднем на каждого работодателя приходится две вакансии.*


# Юнит 4. Детальный анализ вакансий

1. Напишите запрос, который позволит узнать, сколько (cnt) вакансий в каждом регионе (area).
Отсортируйте по количеству вакансий в порядке убывания.

In [12]:
query_4_1 = f'''select a.name, count(*) 
    --столбцы к выдаче: название региона и количество вакансий
    from vacancies v
    --соединим таблицы с вакансиями и регионами 
    --с помощью left join
    left join areas a on v.area_id = a.id 
    group by a.name --делаем группировку по регионам
    order by 2 desc --отсортируем по убыванию
    limit 5 --выведем первые 5 строк
'''

In [13]:
df = pd.read_sql_query(query_4_1, connection)
df

/tmp/ipykernel_48748/347208320.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_4_1, connection)


name  count
0           Москва   5333
1  Санкт-Петербург   2851
2            Минск   2112
3      Новосибирск   2006
4           Алматы   1892

2. Напишите запрос, чтобы определить у какого количества вакансий заполнено хотя бы одно из двух полей с зарплатой.

In [14]:
query_4_2 = f'''select count(*)
    from vacancies v 
    --установим условие, что хотя бы 
    --одно из полей с зарплатой заполнено
    where (v.salary_from is not null)
        or (v.salary_to is not null)
'''

In [15]:
df = pd.read_sql_query(query_4_2, connection)
print(f"В {df['count'].iloc[0]} вакансий заполнено хотя бы одно из двух полей с зарплатой")

В 24073 вакансий заполнено хотя бы одно из двух полей с зарплатой


/tmp/ipykernel_48748/3235451656.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_4_2, connection)


3. Найдите средние значения для нижней и верхней границы зарплатной вилки. Округлите значения до целого.

In [16]:
# выведем средние границы зарплатной вилки 
# с помощью агрегатной функции avg
query_4_3 = f'''select avg(v.salary_from) low, 
    avg(v.salary_to) high
    from vacancies v
'''

In [17]:
df = pd.read_sql_query(query_4_3, connection)
print(f"Средняя нижняя граница зарплатной вилки - {round(df['low'].iloc[0], 0)} рублей")
print(f"Средняя верхняя граница зарплатной вилки - {round(df['high'].iloc[0], 0)} рублей")

Средняя нижняя граница зарплатной вилки - 71065.0 рублей
Средняя верхняя граница зарплатной вилки - 110537.0 рублей


/tmp/ipykernel_48748/3318877451.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_4_3, connection)


4. Напишите запрос, который выведет количество вакансий для каждого сочетания типа рабочего графика (schedule) и типа трудоустройства (employment), используемого в вакансиях. Результат отсортируйте по убыванию количества.


In [18]:
query_4_4 = f'''select v.schedule, v.employment, count(*)
    --выведем столбцы с графиком, типом трудоустройства
    --и количеством вакансий
    from vacancies v
    --установим группировку по графику и типу трудоустройства
    group by v.schedule, v.employment
    order by 3 desc --сортируем по убыванию кол-ва вакансий
    offset 1 --для вывода второго места игнорируем первое
    limit 1 --ограничиваем вывод одной строкой
'''

In [19]:
df = pd.read_sql_query(query_4_4, connection)
df

/tmp/ipykernel_48748/2981602351.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_4_4, connection)


schedule        employment  count
0  Удаленная работа  Полная занятость   7802

5. Напишите запрос, выводящий значения поля Требуемый опыт работы (experience) в порядке возрастания количества вакансий, в которых указан данный вариант опыта. 

In [20]:
query_4_5 = f'''select v.experience, count(*)
    --столбцы к выдаче: опыт работы и кол-во вакансий
    from vacancies v
    --используем группировку по опыту
    group by v.experience
    --сортируем по возрастанию кол-ва вакансий
    order by 2 
'''

In [21]:
df = pd.read_sql_query(query_4_5, connection)
df

/tmp/ipykernel_48748/2601166264.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query_4_5, connection)


experience  count
0         Более 6 лет   1337
1           Нет опыта   7197
2       От 3 до 6 лет  14511
3  От 1 года до 3 лет  26152

***

In [22]:
# построим диаграмму распределения зарплат
# начнем с SQL запроса
query_salary = f'''select v.salary_from low, 
    v.salary_to high
    --выведем столбцы с нижним и верхним порогом зарплат
    from vacancies v
'''
# сохраняем полученную таблицу в переменной df_salary
df_salary = pd.read_sql_query(query_salary, connection)

# построим теперь коробчатую диаграмму
fig = px.box(
    data_frame=df_salary,
    title='Распределение верхнего и нижнего порога зарплат'
)
fig.update_xaxes(dict(title='Порог зарплат', zeroline=False))
fig.update_yaxes(dict(title='Зарплата, руб.', zeroline=False))
fig.show();

/tmp/ipykernel_48748/3413619807.py:9: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_salary = pd.read_sql_query(query_salary, connection)


### *Выводы по детальному анализу данных*

- *Вакансии представлены не только по России. Можно заметить вакансии в Республике Беларусь, Казахстане, Грузии, Армении, Кипре и др.*
- *Многие работодатели неохотно указывают данные по зарплате: только в половине вакансий указан минимальный или максимальный порог. Скорее всего такие работодатели предпочитают обсуждать зарплатные ожидания только с кандидатами, максимально подходящими по опыту.*
- *На мой взгляд, средние показатели по зарплатам не отражают реальное распределение. Предпочтительней использовать медианные значения (см. график выше). Вилка медианных зарплат находится от 50000 рублей до 80000 рублей, в то время как средние показатели той же вилки - от 71000 до 110000 рублей соответственно.* 
- *В подавляющем количестве вакансий требуются сотрудники для работы в офисе (или предприятии) на полный рабочий день. Вакансии с удаленным типом работы на втором месте по количеству. Вместе они составляют 85% от общего числа вакансий.*
- *В статистике по опыту можно заметить, что работодатели гораздо сильнее заинтересованы с работниках с минимальным опытом и значительно реже ищут сотрудников без опыта.*

# Юнит 5. Анализ работодателей

1. Напишите запрос, который позволит узнать, какие работодатели находятся на первом и пятом месте по количеству вакансий.

In [23]:
query_5_1 = f'''(select e.name, count(*)
    --выведем столбцы с работодателем и 
    --количеством вакансий
    from vacancies v 
    --объединим таблицы с вакансиями и работодателями
    left join employers e on v.employer_id = e.id
    --установим группировку по работодателям
    group by e.name
    --сортируем по убыванию количества вакансий
    order by 2 desc
    --выведем только первую строку
    limit 1)    
    union all --используем объединение таблиц
    (select e.name, count(*)
    from vacancies v
    left join employers e on v.employer_id = e.id
    group by e.name
    order by 2 desc
    --опустим верхние 4 строки
    offset 4
    --и выведем только 5ю
    limit 1)   
'''

In [24]:
df = pd.read_sql_query(query_5_1, connection)
df

/tmp/ipykernel_48748/1792814825.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name  count
0         Яндекс   1933
1  Газпром нефть    331

2. Напишите запрос, который для каждого региона выведет количество работодателей и вакансий в нём.
Среди регионов, в которых нет вакансий, найдите тот, в котором наибольшее количество работодателей.


In [25]:
query_5_2 = f'''select a.name region,
        count(distinct e.id) cnt_employers,
        count(distinct v.id) cnt_vacancies
    --выведем столбцы: регион, кол-во работодателей
    --и количество вакансий
    from areas a
    --последовательно соединим таблицу с регионами 
    --с таблицами с вакансиями и с работодателями
    left join vacancies v on a.id = v.area_id
    left join employers e on a.id = e.area
    --поставим условие поиска отсутствующих вакансий
    where v.name is null
    --группируем по региону
    group by 1
    --сортируем по убыванию числа работодателей
    order by 2 desc
    --выводим верхнюю строку
    limit 1
'''

In [26]:
df = pd.read_sql_query(query_5_2, connection)
df

/tmp/ipykernel_48748/3341481329.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



region  cnt_employers  cnt_vacancies
0  Россия            410              0

3. Для каждого работодателя посчитайте количество регионов, в которых он публикует свои вакансии. Отсортируйте результат по убыванию количества.


In [27]:
query_5_3 = f'''select e.name, 
        count(distinct v.area_id) cnt_areas
    --столбцы к выдаче: работодатель, кол-во регионов
    from employers e
    --последовательно соединим таблицу с работодателями 
    --с таблицами с вакансиями и с регионами 
    left join areas a on e.area = a.id
    left join vacancies v on e.id = v.employer_id
    --группируем по работодателям
    group by 1
    --сортируем по убыванию вакансий
    order by 2 desc
    --выводим верхнюю строку
    limit 1
'''

In [28]:
df = pd.read_sql_query(query_5_3, connection)
df

/tmp/ipykernel_48748/2398953733.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name  cnt_areas
0  Яндекс        181

4. Напишите запрос для подсчёта количества работодателей, у которых не указана сфера деятельности. 

In [29]:
query_5_4 = f'''select count(e.id)
    --выводим агрегатную функцию подсчета работодателей
    from employers e
    --соединяем таблицы с работодателями и 
    --сферами деятельности
    left join employers_industries ei on e.id = ei.employer_id
    --устанавливаем условие, что сфера деятельности не указана
    where ei.industry_id is null    
'''

In [30]:
df = pd.read_sql_query(query_5_4, connection)
print(f"В базе {df['count'].iloc[0]} работодателей, у которых не указана сфера деятельности")

В базе 8419 работодателей, у которых не указана сфера деятельности


/tmp/ipykernel_48748/1464602064.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



5. Напишите запрос, чтобы узнать название компании, находящейся на третьем месте в алфавитном списке (по названию) компаний, у которых указано четыре сферы деятельности. 

In [31]:
query_5_5 = f'''select e.name
    --столбцы к выдаче: имя работодателя
    from employers e
    --соединяем таблицы с работодателями и 
    --сферами деятельности
    left join employers_industries ei on e.id = ei.employer_id
    --группируем по id работодателя
    group by e.id
    --устанавливаем фильтр по работодателям с
    --четырьмя сферами деятельности
    having count(ei.industry_id) = 4
    --сортируем в алфавитном порядке
    --по имени работодателя
    order by 1
    --для вывода третьего места игнорируем первые два
    offset 2
    --выводим самую верхнюю строку
    limit 1
'''

In [32]:
df = pd.read_sql_query(query_5_5, connection)
df

/tmp/ipykernel_48748/1650419958.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name
0  2ГИС

6. С помощью запроса выясните, у какого количества работодателей в качестве сферы деятельности указана Разработка программного обеспечения.


In [33]:
query_5_6 = f'''select count(ei.employer_id)
    --столбцы к выводу: число работодателей
    from employers_industries ei
    --соединим таблицы работодателей и сферы деятельности
    left join industries i on ei.industry_id = i.id
    --установим фильтр поиска ключевых слов 
    --в сферах деятельности
    where i.name like '%Разработка программного обеспечения%'
'''

In [34]:
df = pd.read_sql_query(query_5_6, connection)
print(f"В базе {df['count'].iloc[0]} работодателей, у которых в качестве сферы деятельности указана «Разработка программного обеспечения»")

В базе 3553 работодателей, у которых в качестве сферы деятельности указана «Разработка программного обеспечения»


/tmp/ipykernel_48748/1364908599.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



7. Для компании «Яндекс» выведите список регионов-миллионников, в которых представлены вакансии компании, вместе с количеством вакансий в этих регионах. Также добавьте строку Total с общим количеством вакансий компании. Результат отсортируйте по возрастанию количества.

Список городов-милионников надо взять [отсюда](https://ru.wikipedia.org/wiki/%D0%93%D0%BE%D1%80%D0%BE%D0%B4%D0%B0-%D0%BC%D0%B8%D0%BB%D0%BB%D0%B8%D0%BE%D0%BD%D0%B5%D1%80%D1%8B_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8). 

Если возникнут трудности с этим задание посмотрите материалы модуля  PYTHON-17. Как получать данные из веб-источников и API. 

In [35]:
# воспользуемся библиотеками requests и BeautifulSoup
# для создания списка городов миллионеров
url = 'https://ru.wikipedia.org/wiki/%D0%93%D0%BE%D1%80%D0%BE%D0%B4%D0%B0-%D0%BC%D0%B8%D0%BB%D0%BB%D0%B8%D0%BE%D0%BD%D0%B5%D1%80%D1%8B_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8'
response = requests.get(url)
page = BeautifulSoup(response.text, 'html.parser')
# ищем нужную таблицу по ключевым словам из разметки сайта
wiki_table = page.find('table', {'class':"standard"})
df = pd.read_html(str(wiki_table))
# преобразуем в привычный нам датафрейм
df = pd.DataFrame(df[0])
# создадим из столбца с городами список
mln_cities = df['Город'].to_list()
# исправим название города Воронеж
mln_cities[13] = 'Воронеж'
# список готов
mln_cities

['Москва',
 'Санкт-Петербург',
 'Новосибирск',
 'Екатеринбург',
 'Казань',
 'Нижний Новгород',
 'Челябинск',
 'Красноярск',
 'Самара',
 'Уфа',
 'Ростов-на-Дону',
 'Омск',
 'Краснодар',
 'Воронеж',
 'Пермь',
 'Волгоград']

In [36]:
query_5_7 = f'''(select a.name, 
        count(v.id) cnt
    --столбцы к выводу: название региона, число вакансий
    from vacancies v 
    --последовательно соединим таблицу с вакансиями  
    --с таблицами с работодателями и с регионами 
    join employers e on e.id = v.employer_id
    join areas a on v.area_id = a.id
    --ставим фильтр по названию организации и
    --условие, что город включен в список миллионников
    where e.name = 'Яндекс' 
        and a.name in {tuple(mln_cities)}
    --группируем по названию региона
    group by 1
    --сортируем по убыванию кол-ва вакансий    
    order by 2 desc)
    
    --используем объединение таблиц
    union all
    
    (select 'total', count(*)
    --выводим текст 'total' в первом столбце и 
    --счетчик всех вакансий во втором
    from vacancies v 
    --последовательно соединим таблицу с вакансиями  
    --с таблицами с работодателями и с регионами 
    join employers e on e.id = v.employer_id
    join areas a on v.area_id = a.id
    --ставим фильтр по названию организации и
    --условие, что город включен в список миллионников
    where e.name = 'Яндекс' 
        and a.name in {tuple(mln_cities)})
'''

In [37]:
df = pd.read_sql_query(query_5_7, connection)
df

/tmp/ipykernel_48748/3129374555.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name  cnt
0             total  485
1            Москва   54
2   Санкт-Петербург   42
3      Екатеринбург   39
4   Нижний Новгород   36
5       Новосибирск   35
6           Воронеж   32
7         Краснодар   30
8            Самара   26
9               Уфа   26
10           Казань   25
11            Пермь   25
12   Ростов-на-Дону   25
13        Волгоград   24
14       Красноярск   23
15        Челябинск   22
16             Омск   21

***

In [38]:
# напишем запрос, который выведет наиболее часто
# встречающиеся сферы деятельности у работодателей

query_5 = f'''select i.name ind, count(e.name) cnt
    --столбцы к выводу: сфера деятельности,
    --кол-во работодателей
    from employers_industries ei
    --последовательно соединим таблицу с id работодателя/индустрии
    --с таблицами названий работодателей и сфер деятельности
    left join employers e on ei.employer_id = e.id
    left join industries i on ei.industry_id = i.id
    --группируем по сфере деятельности
    group by 1
    --сортируем по убыванию числа работодателей
    order by 2 desc
    --посмотрим на топ-10 результатов
    limit 10
'''

df = pd.read_sql_query(query_5, connection)
df

/tmp/ipykernel_48748/850431177.py:20: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



ind   cnt
0                Разработка программного обеспечения  3553
1  Системная интеграция,  автоматизации технологи...  2993
2  Интернет-компания (поисковики, платежные систе...  1675
3  Маркетинговые, рекламные, BTL, дизайнерские, E...   798
4                              Консалтинговые услуги   662
5                                 Кадровые агентства   389
6  Электронно-вычислительная, оптическая, контрол...   374
7                       Розничная сеть (продуктовая)   368
8                                   Интернет-магазин   351
9                        Архитектура, проектирование   346

### *Выводы по анализу работодателей*

- *В топ-10 работодателей по количеству вакансий входят в основном компании, связанные с информационными технологиями и активно внедряющие высокотехнологичные решения. Таким образом, мы можем сделать вывод, что спрос на IT специалистов достаточно велик.*
 - *Также, проанализировав наиболее популярные сферы деятельности у работодателей, можно заметить, что разработка ПО, системная интеграция и интернет технологии с существенным отрывом лидируют среди остальных отраслей. Это может означать, что ведение бизнеса, связанного с этими сферами, рентабельно: есть спрос на данные услуги и компании получают достаточную прибыль для покрытия издержек и дальнейшего роста.*

# Юнит 6. Предметный анализ

1. Сколько вакансий имеет отношение к данным?

Считаем, что вакансия имеет отношение к данным, если в её названии содержатся слова 'data' или 'данн'.

*Подсказка: Обратите внимание, что названия вакансий могут быть написаны в любом регистре.* 


In [39]:
query_6_1 = f'''select count(*)
    --столбцы к выдаче: количество вакансий
    from vacancies v
    --фильтруем результаты по ключевым словам
    where lower(v.name) like '%данн%' 
        or lower(v.name) like '%data%'
'''

In [40]:
df = pd.read_sql_query(query_6_1, connection)
print(f"В базе {df['count'].iloc[0]} вакансий, которые имеют отношение к данным")

В базе 1771 вакансий, которые имеют отношение к данным


/tmp/ipykernel_48748/3429054774.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



2. Сколько есть подходящих вакансий для начинающего дата-сайентиста? 
Будем считать вакансиями для дата-сайентистов такие, в названии которых есть хотя бы одно из следующих сочетаний:
* 'data scientist'
* 'data science'
* 'исследователь данных'
* 'ML' (здесь не нужно брать вакансии по HTML)
* 'machine learning'
* 'машинн%обучен%'

** В следующих заданиях мы продолжим работать с вакансиями по этому условию.*

Считаем вакансиями для специалистов уровня Junior следующие:
* в названии есть слово 'junior' *или*
* требуемый опыт — Нет опыта *или*
* тип трудоустройства — Стажировка.
 

In [41]:
query_6_2 = f'''select count(*)
    --столбцы к выдаче: количество вакансий
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and 
        (lower(v.name) like '%junior%'
        or v.experience = 'Нет опыта'
        or v.employment = 'Стажировка')
'''

In [42]:
df = pd.read_sql_query(query_6_2, connection)
print(f"В базе {df['count'].iloc[0]} подходящая вакансия для начинающего дата-сайентиста")

В базе 51 подходящая вакансия для начинающего дата-сайентиста


/tmp/ipykernel_48748/2589130298.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



3. Сколько есть вакансий для DS, в которых в качестве ключевого навыка указан SQL или postgres?

** Критерии для отнесения вакансии к DS указаны в предыдущем задании.*

In [43]:
query_6_3 = f'''select count(*)
    --столбцы к выдаче: количество вакансий
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and
        (lower(v.key_skills) like '%sql%'
        or lower(v.key_skills) like '%postgres%')
'''

In [44]:
df = pd.read_sql_query(query_6_3, connection)
print(f"В базе {df['count'].iloc[0]} вакансия для DS, в которых в качестве ключевого навыка указан SQL или postgres")

/tmp/ipykernel_48748/3703094384.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



В базе 201 вакансия для DS, в которых в качестве ключевого навыка указан SQL или postgres


4. Проверьте, насколько популярен Python в требованиях работодателей к DS.Для этого вычислите количество вакансий, в которых в качестве ключевого навыка указан Python.

** Это можно сделать помощью запроса, аналогичного предыдущему.*

In [45]:
query_6_4 = f'''select count(*)
    --столбцы к выдаче: количество вакансий
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and
        (lower(v.key_skills) like '%python%')
'''

In [46]:
df = pd.read_sql_query(query_6_4, connection)
print(f"В базе {df['count'].iloc[0]} вакансия для DS, в которых в качестве ключевого навыка указан Python")

В базе 351 вакансия для DS, в которых в качестве ключевого навыка указан Python


/tmp/ipykernel_48748/1301038707.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



5. Сколько ключевых навыков в среднем указывают в вакансиях для DS?
Ответ округлите до двух знаков после точки-разделителя.

In [47]:
query_6_5 = f'''select avg(
            length(v.key_skills)
            -length(replace(v.key_skills, CHR(9), ''))
            +1
            )
    --выведем среднее число навыков, предварительно разделив
    --их пробелами и прибавив единицу 
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and v.key_skills is not null
'''

In [48]:
df = pd.read_sql_query(query_6_5, connection)
print(f"{round(df['avg'].iloc[0], 2)} ключевых навыков в среднем указывают в вакансиях для DS")

/tmp/ipykernel_48748/748901162.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



6.41 ключевых навыков в среднем указывают в вакансиях для DS


6. Напишите запрос, позволяющий вычислить, какую зарплату для DS в **среднем** указывают для каждого типа требуемого опыта (уникальное значение из поля *experience*). 

При решении задачи примите во внимание следующее:
1. Рассматриваем только вакансии, у которых заполнено хотя бы одно из двух полей с зарплатой.
2. Если заполнены оба поля с зарплатой, то считаем зарплату по каждой вакансии как сумму двух полей, делённую на 2. Если заполнено только одно из полей, то его и считаем зарплатой по вакансии.
3. Если в расчётах участвует null, в результате он тоже даст null (посмотрите, что возвращает запрос select 1 + null). Чтобы избежать этой ситуацию, мы воспользуемся функцией [coalesce](https://postgrespro.ru/docs/postgresql/9.5/functions-conditional#functions-coalesce-nvl-ifnull), которая заменит null на значение, которое мы передадим. Например, посмотрите, что возвращает запрос `select 1 + coalesce(null, 0)`

Выясните, на какую зарплату в среднем может рассчитывать дата-сайентист с опытом работы от 3 до 6 лет. Результат округлите до целого числа. 

In [49]:
query_6_6 = f'''select avg(
        coalesce(
            (v.salary_from+v.salary_to)/2, 
            v.salary_from, 
            v.salary_to, 
            0
            )
        )
    --выведем среднюю зарплату, воспользовавшись функцией
    --coalesce для устранения из выборки пустых значений
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and 
        (v.salary_from is not null 
        or v.salary_to is not null)
        and v.experience = 'От 3 до 6 лет'
'''

In [50]:
df = pd.read_sql_query(query_6_6, connection)
print(f"На зарплату {round(df['avg'].iloc[0], 0)} рублей в среднем может рассчитывать дата-сайентист с опытом работы от 3 до 6 лет")

На зарплату 243115.0 рублей в среднем может рассчитывать дата-сайентист с опытом работы от 3 до 6 лет


/tmp/ipykernel_48748/2070519518.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



***

In [51]:
# дополнительно оценим зависимость среднего числа указываемых 
# ключевых навыков и средней заработной платы от опыта 
# дата саентиста
query_6 = f'''select 
            v.experience,
            avg(length(v.key_skills)
            -length(replace(v.key_skills, CHR(9), ''))
            +1) avg_skill,
            avg(coalesce(
            (v.salary_from+v.salary_to)/2, 
            v.salary_from, 
            v.salary_to, 
            0)) avg_salary
    --выведем столбцы: опыт, среднее число навыков, 
    --средняя зарплата
    from vacancies v
    --фильтруем результаты по ключевым словам и условиям
    where (lower(v.name) like '%data scientist%' 
        or lower(v.name) like '%data science%'
        or lower(v.name) like '%исследователь данных%'
        or (v.name like '%ML%' 
            and v.name not like '%HTML%')
        or lower(v.name) like '%machine learning%'
        or lower(v.name) like '%машинн%обучен%')
        and v.key_skills is not null
        and
        (v.salary_from is not null 
        or v.salary_to is not null)
    --делаем группировку по опыту
    group by v.experience
    --сортируем по убыванию средней зарплаты
    order by 3 desc
'''

df = pd.read_sql_query(query_6, connection)
df

/tmp/ipykernel_48748/3616293738.py:35: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



experience  avg_skill     avg_salary
0       От 3 до 6 лет   5.444444  243114.666667
1  От 1 года до 3 лет   6.833333  146703.875000
2           Нет опыта   7.714286   74642.857143

### *Выводы по предметному анализу*

- *Нам удалось выяснить, что более 3% вакансий так или иначе связаны с данными. Это подтверждает высокий уровень спроса на специалистов в данной области.*
- *Однако, количество вакансий для начинающих дата сайентистов очень низкое. Это может говорить о перенасыщенности рынка  выпускниками курсов и студентами, у которых еще нет опыта и конкуренция на данном уровне очень высокая. Также можно предположить, что работодатели больше заитересованы в трудоустройстве кандидатов с опытом.*
- *Зарплаты в области data science начинаются от 70000 руб. и имеют быструю динамику роста с каждым годом полученного опыта.*
- *Интересной выглядит статистика указываемых работодателем ключевых навыков. С опытом среднее число ключевых навыков уменьшается. Это говорит о том, что кандидат с большим опытом имеет больше ключевых навыков, что позволяет не указывать их все в вакансии. Но и можно заметить, что планка навыков завышается для начальных позиций, что подтверждает высокий уровень конкуренции в отрасли.* 

# Общий вывод по проекту

*Основываясь на анализе базы данных, мы определили, что на рынке сохраняется дефицит опытных кандидатов в IT секторе. Многие высокотехнологичные компании предлагают конкурентные заплаты для привлечения лучших талантов. При этом чем больше город, тем большую заработную плату он предлагает. Наибольшее число вакансий в крупнейших городах РФ и СНГ наблюдается по таким напралениям как разработка ПО и системная интеграция. Стоит отметить, что работодатели заинтересованы в трудоустройстве кандидатов с опытом. Те кандидаты, у кого нет опыта вероятнее всего столкнутся с высокой конкуренцией. Им также предстоит овладеть бОльшим числом навыков, чтобы потенциальный работодатель их заметил.*

In [52]:
# проведем дополнительный анализ заработной платы 
# в различных сферах деятельности
query_7_1 = f'''select i.name,
            avg(coalesce(
            (v.salary_from+v.salary_to)/2, 
            v.salary_from, 
            v.salary_to, 
            0))
    --выведем название сферы деятельности и среднюю зарплату, 
    --воспользовавшись функцией coalesce для устранения из 
    --выборки пустых значений
    from vacancies v 
    left join employers e on e.id = v.employer_id
    left join employers_industries ei on e.id = ei.employer_id
    left join industries i on ei.industry_id = i.id
    --фильтруем результаты по ключевым словам и условиям
    where v.salary_from is not null 
        or v.salary_to is not null
    --сгруппируем по сфере деятельности
    group by i.name
    --для лучшей выборки отсеим вкансии которые встречаются 
    --больше 100 раз 
    having count(v.id) > 100
    --отсортируем по убыванию
    order by 2 desc
'''

df = pd.read_sql_query(query_7_1, connection)
df

/tmp/ipykernel_48748/3537402598.py:28: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name            avg
0                                  Кадровые агентства  144529.656821
1   Дорожно-строительная техника, сельскохозяйстве...  119919.132075
2   Оборудование для пищевой промышленности, упако...  119656.169811
3   Финансово-кредитное посредничество (биржа, бро...  117714.286458
4                 Разработка программного обеспечения  117658.561461
..                                                ...            ...
69                        Государственные организации   58507.712707
70                Безопасность, охранная деятельность   56957.284483
71                               Оптоволоконная связь   52335.211161
72                                    Мобильная связь   52299.932615
73                                Фиксированная связь   49625.617997

[74 rows x 2 columns]

In [53]:
# проведем дополнительный анализ зависимости 
# средней заработной платы от региона
query_7_2 = f'''select a.name,
            avg(coalesce(
            (v.salary_from+v.salary_to)/2, 
            v.salary_from, 
            v.salary_to, 
            0))
    --выведем название сферы деятельности и среднюю зарплату, 
    --воспользовавшись функцией coalesce для устранения из 
    --выборки пустых значений
    from vacancies v 
    left join areas a on v.area_id = a.id
    --фильтруем результаты по ключевым словам и условиям
    where v.salary_from is not null 
        or v.salary_to is not null
    --сгруппируем по сфере деятельности
    group by a.name
    --для лучшей выборки отсеим регионы, в которых 
    --меньше 100 вакансий
    having count(v.id) > 100
    --отсортируем по убыванию
    order by 2 desc    
'''

df = pd.read_sql_query(query_7_2, connection)
df

/tmp/ipykernel_48748/3452603742.py:26: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



name            avg
0                        Армения  219569.726415
1                         Москва  134140.171482
2                    Новосибирск  107776.716900
3                Санкт-Петербург  104409.772236
4                           Сочи   99437.200000
5                          Томск   99318.514286
6                Нижний Новгород   96058.730882
7                          Пермь   95984.659091
8                 Ростов-на-Дону   94065.385621
9                    Калининград   92357.033149
10                     Краснодар   92328.215007
11                        Казань   92207.383758
12                  Екатеринбург   91895.745838
13                         Минск   90425.666008
14                          Омск   86392.957958
15                       Воронеж   84958.184154
16                    Нур-Султан   84326.489971
17                   Владивосток   82727.032911
18                     Ульяновск   81761.548780
19                     Ярославль   80673.808429
20                        Самара   80223.106931
21                        Тюмень   79757.114551
22                      Белгород   79422.285714
23                          Тула   79046.440678
24                     Челябинск   77462.784431
25                    Красноярск   75155.924000
26                           Уфа   74733.127937
27                       Ташкент   74225.045902
28                        Рязань   73599.027778
29  Иваново (Ивановская область)   73289.830508
30                        Алматы   73170.902022
31                         Тверь   72605.974843
32                       Саратов   72285.217593
33                     Хабаровск   70404.560976
34                        Брянск   70306.435644
35                       Иркутск   69938.112281
36                         Курск   69556.818182
37                      Тольятти   69296.255639
38                        Ижевск   69276.863071
39                     Волгоград   68688.505882
40                      Владимир   68423.588710
41                       Барнаул   67481.222642
42                      Кемерово   63373.808824
43                        Липецк   63144.719008
44                   Симферополь   62645.330189
45     Киров (Кировская область)   62131.262136
46                    Ставрополь   61890.967213
47              Набережные Челны   61768.272727
48                      Оренбург   61654.725806
49                   Новокузнецк   59754.711538
50                     Чебоксары   59203.699422
51                         Пенза   56982.551515

In [54]:
# изучим распределение работодателей по регионам и 
# сферам деятельности
query_7_3 = f'''select a.name region,
        i.name ind, count(*) 
    --столбцы к выводу: название региона, 
    --название сферы деятельности, число вакансий  
    from vacancies v 
    --последовательно соединим таблицу с вакансиями с 
    --другими таблицами
    left join employers e on e.id = v.employer_id
    left join employers_industries ei on e.id = ei.employer_id
    left join industries i on ei.industry_id = i.id
    left join areas a on v.area_id = a.id
    --уберем из выдачи те строки, где отсутствует
    --название сферы деятельности
    where i.name is not null
    --сгруппируем по названию региона и сфере
    --деятельности
    group by i.name, a.name
    --отсортируем по убыванию числа вакансий
    order by 3 desc
    --выведем верхние 20 строк
    limit 20
'''

df = pd.read_sql_query(query_7_3, connection)
df

/tmp/ipykernel_48748/1600106880.py:26: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



region                                                ind  count
0            Москва                Разработка программного обеспечения   1294
1            Москва  Системная интеграция,  автоматизации технологи...   1117
2             Минск                Разработка программного обеспечения   1023
3   Санкт-Петербург                Разработка программного обеспечения    908
4            Москва  Интернет-компания (поисковики, платежные систе...    798
5   Санкт-Петербург  Системная интеграция,  автоматизации технологи...    679
6            Москва                                               Банк    603
7       Новосибирск                Разработка программного обеспечения    580
8            Алматы  Системная интеграция,  автоматизации технологи...    539
9   Нижний Новгород                Разработка программного обеспечения    538
10            Минск  Системная интеграция,  автоматизации технологи...    517
11      Новосибирск  Системная интеграция,  автоматизации технологи...    476
12           Алматы                Разработка программного обеспечения    470
13  Нижний Новгород  Системная интеграция,  автоматизации технологи...    461
14  Санкт-Петербург  Интернет-компания (поисковики, платежные систе...    455
15           Казань                Разработка программного обеспечения    415
16     Екатеринбург                Разработка программного обеспечения    393
17     Екатеринбург  Системная интеграция,  автоматизации технологи...    383
18       Нур-Султан  Системная интеграция,  автоматизации технологи...    370
19           Самара  Системная интеграция,  автоматизации технологи...    357